In [1]:
from fastai import datasets
from utils import *
from callbacks import *
from optimizers import *
from data_block import *
from transforms import *
from xresnets import *
from learner import *
import torch.nn.functional as F

In [2]:
path = Path('C:/Users/iamab/Downloads/imagenette2-160')
path.ls()

[WindowsPath('C:/Users/iamab/Downloads/imagenette2-160/train'),
 WindowsPath('C:/Users/iamab/Downloads/imagenette2-160/val'),
 WindowsPath('C:/Users/iamab/Downloads/imagenette2-160/wandb')]

In [3]:
def grandparent_splitter(o,name): return True if o.parent.parent.name == name else False
def parent_name(o): return o.parent.name

In [4]:
tfms = [into_rgb, ResizeFixed(128), np_to_float, PIL_FLIP(0.5)]
il = ImageList.from_path(path, tfms = tfms)
sl = SplitDataset.from_func(il, partial(grandparent_splitter, name = 'val'))
ll = label_train_valid(sl, func = parent_name, procy= Processor())

In [5]:
data = ll.to_databunch(train_bs=64)

In [6]:
model = xresnet34(init_func = 'kaiming_normal_')

In [7]:
sched = combine_scheds(create_phases(0.2), cos_annealer(0.001,0.1,0.01))
cbfs = [CudaCallback, normalise_callback(data), partial(AvgStatsCallback, accuracy), NewRecorderCallback, 
        partial(NewParamSchedulerCallback, 'lr', sched), WandbCallback, ProgressCallback]

In [25]:
wandb.init(name = 'without_lookahead', project = 'learning',entity = 'a_bhimanyu',
           dir = 'C:/Users/iamab/Downloads/imagenette2-160')

opt = partial(StatefulOptimizer, 
              steppers = [momentum_step, weight_decay], 
              stats = [AverageGrad()], 
              lr =0.01,wd = 1e-04)

learn = Learner(model, data, loss_func=F.cross_entropy, opt_func=opt, cb_funcs=cbfs)

W&B Run: https://app.wandb.ai/a_bhimanyu/learning/runs/1xqv2t5t

## Learning without Lookahead

In [28]:
learn.fit(30)

Better model found at epoch 0 with valid_loss value: 1.2852838039398193.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200707_140942-1xqv2t5t\\bestmodel.pth'>
Better model found at epoch 6 with valid_loss value: 1.039011836051941.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200707_140942-1xqv2t5t\\bestmodel.pth'>
Better model found at epoch 11 with valid_loss value: 0.8428086042404175.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200707_140942-1xqv2t5t\\bestmodel.pth'>
Better model found at epoch 18 with valid_loss value: 0.6517592668533325.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200707_140942-1xqv2t5t\\bestmodel.pth'>
Loading model state from <_io.BufferedReader name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200707_14

## Learning with Lookahead

In [8]:
wandb.init(name = 'with_lookahead', project = 'learning',entity = 'a_bhimanyu',
           dir = 'C:/Users/iamab/Downloads/imagenette2-160')

W&B Run: https://app.wandb.ai/a_bhimanyu/learning/runs/1r0eunbd

In [9]:
opt = partial(StatefulOptimizer, 
              steppers = [momentum_step, weight_decay, lookahead_step], 
              stats = [AverageGrad(), Step(), LookAheadStat()], 
              lr =0.01,wd = 1e-04)

learn = Learner(model, data, loss_func=F.cross_entropy, opt_func=opt, cb_funcs=cbfs)

In [10]:
learn.fit(30)

Better model found at epoch 0 with valid_loss value: 2.597832202911377.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200708_105520-1r0eunbd\\bestmodel.pth'>
Better model found at epoch 2 with valid_loss value: 1.5168195962905884.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200708_105520-1r0eunbd\\bestmodel.pth'>


requests_with_retry encountered retryable exception: ('Connection aborted.', ConnectionResetError(10054, 'An existing connection was forcibly closed by the remote host', None, 10054, None)). args: ('https://api.wandb.ai/files/a_bhimanyu/learning/1r0eunbd/file_stream',), kwargs: {'json': {'files': {'wandb-events.jsonl': {'offset': 33, 'content': ['{"system.gpu.0.gpu": 88.4, "system.gpu.0.memory": 85.2, "system.gpu.0.memoryAllocated": 42.8, "system.gpu.0.temp": 77.27, "system.gpu.process.0.gpu": 88.4, "system.gpu.process.0.memory": 85.2, "system.gpu.process.0.memoryAllocated": 42.8, "system.gpu.process.0.temp": 77.27, "system.cpu": 40.02, "system.memory": 78.99, "system.disk": 47.9, "system.proc.memory.availableMB": 1687.1, "system.proc.memory.rssMB": 1956.38, "system.proc.memory.percent": 24.36, "system.proc.cpu.threads": 27.0, "system.network.sent": 10998747, "system.network.recv": 846479, "_wandb": true, "_timestamp": 1594206813, "_runtime": 1208}\n']}, 'wandb-history.jsonl': {'offset

Exception in thread Thread-42:
Traceback (most recent call last):
  File "C:\Users\iamab\Anaconda3\lib\threading.py", line 926, in _bootstrap_inner
    self.run()
  File "C:\Users\iamab\Anaconda3\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "C:\Users\iamab\Anaconda3\lib\site-packages\wandb\stats.py", line 92, in _thread_body
    stats = self.stats()
  File "C:\Users\iamab\Anaconda3\lib\site-packages\wandb\stats.py", line 132, in stats
    handle = pynvml.nvmlDeviceGetHandleByIndex(i)
  File "C:\Users\iamab\Anaconda3\lib\site-packages\pynvml.py", line 807, in nvmlDeviceGetHandleByIndex
    _nvmlCheckReturn(ret)
  File "C:\Users\iamab\Anaconda3\lib\site-packages\pynvml.py", line 310, in _nvmlCheckReturn
    raise NVMLError(ret)
pynvml.NVMLError_OperatingSystem: The operating system has blocked the request.



Better model found at epoch 5 with valid_loss value: 1.2897378206253052.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200708_105520-1r0eunbd\\bestmodel.pth'>
Better model found at epoch 9 with valid_loss value: 1.1804046630859375.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200708_105520-1r0eunbd\\bestmodel.pth'>
Better model found at epoch 10 with valid_loss value: 1.0858614444732666.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200708_105520-1r0eunbd\\bestmodel.pth'>
Better model found at epoch 12 with valid_loss value: 0.8860884308815002.
Saving model state at <_io.BufferedWriter name='C:\\Users\\iamab\\Downloads\\imagenette2-160\\wandb\\run-20200708_105520-1r0eunbd\\bestmodel.pth'>


requests_with_retry encountered retryable exception: ('Connection aborted.', ConnectionResetError(10054, 'An existing connection was forcibly closed by the remote host', None, 10054, None)). args: ('https://api.wandb.ai/files/a_bhimanyu/learning/1r0eunbd/file_stream',), kwargs: {'json': {'files': {'wandb-history.jsonl': {'offset': 3485, 'content': ['{"lrs": 0.061779986516372856, "train_losses": 0.7698876857757568, "train_acc": 0.8100199103355408, "_runtime": 8044.444728851318, "_timestamp": 1594213649.5486119, "_step": 3485}\n', '{"lrs": 0.061740628959169375, "train_losses": 0.5024967789649963, "train_acc": 0.8104084730148315, "_runtime": 8045.913047790527, "_timestamp": 1594213651.0169308, "_step": 3486}\n', '{"lrs": 0.0617012767358927, "train_losses": 0.5894423127174377, "train_acc": 0.8104248046875, "_runtime": 8047.421411991119, "_timestamp": 1594213652.525295, "_step": 3487}\n', '{"lrs": 0.06166192457626796, "train_losses": 0.6603490710258484, "train_acc": 0.8103197813034058, "_ru

...

Retry attempt failed:
Traceback (most recent call last):
  File "C:\Users\iamab\Anaconda3\lib\site-packages\urllib3\connection.py", line 160, in _new_conn
    (self._dns_host, self.port), self.timeout, **extra_kw
  File "C:\Users\iamab\Anaconda3\lib\site-packages\urllib3\util\connection.py", line 61, in create_connection
    for res in socket.getaddrinfo(host, port, family, socket.SOCK_STREAM):
  File "C:\Users\iamab\Anaconda3\lib\socket.py", line 752, in getaddrinfo
    for res in _socket.getaddrinfo(host, port, family, type, proto, flags):
socket.gaierror: [Errno 11001] getaddrinfo failed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "C:\Users\iamab\Anaconda3\lib\site-packages\urllib3\connectionpool.py", line 677, in urlopen
    chunked=chunked,
  File "C:\Users\iamab\Anaconda3\lib\site-packages\urllib3\connectionpool.py", line 381, in _make_request
    self._validate_conn(conn)
  File "C:\Users\iamab\Anaconda3\lib\sit

requests_with_retry encountered retryable exception: HTTPSConnectionPool(host='api.wandb.ai', port=443): Max retries exceeded with url: /files/a_bhimanyu/learning/1r0eunbd/file_stream (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x00000215B3FE1408>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed')). args: ('https://api.wandb.ai/files/a_bhimanyu/learning/1r0eunbd/file_stream',), kwargs: {'json': {'files': {'wandb-history.jsonl': {'offset': 3485, 'content': ['{"lrs": 0.061779986516372856, "train_losses": 0.7698876857757568, "train_acc": 0.8100199103355408, "_runtime": 8044.444728851318, "_timestamp": 1594213649.5486119, "_step": 3485}\n', '{"lrs": 0.061740628959169375, "train_losses": 0.5024967789649963, "train_acc": 0.8104084730148315, "_runtime": 8045.913047790527, "_timestamp": 1594213651.0169308, "_step": 3486}\n', '{"lrs": 0.0617012767358927, "train_losses": 0.5894423127174377, "train_acc": 0.8104248046875, "_runtime": 8047.421

requests_with_retry encountered retryable exception: HTTPSConnectionPool(host='api.wandb.ai', port=443): Max retries exceeded with url: /files/a_bhimanyu/learning/1r0eunbd/file_stream (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x00000215B3FE1408>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed')). args: ('https://api.wandb.ai/files/a_bhimanyu/learning/1r0eunbd/file_stream',), kwargs: {'json': {'files': {'wandb-history.jsonl': {'offset': 3485, 'content': ['{"lrs": 0.061779986516372856, "train_losses": 0.7698876857757568, "train_acc": 0.8100199103355408, "_runtime": 8044.444728851318, "_timestamp": 1594213649.5486119, "_step": 3485}\n', '{"lrs": 0.061740628959169375, "train_losses": 0.5024967789649963, "train_acc": 0.8104084730148315, "_runtime": 8045.913047790527, "_timestamp": 1594213651.0169308, "_step": 3486}\n', '{"lrs": 0.0617012767358927, "train_losses": 0.5894423127174377, "train_acc": 0.8104248046875, "_runtime": 8047.421

requests_with_retry encountered retryable exception: HTTPSConnectionPool(host='api.wandb.ai', port=443): Max retries exceeded with url: /files/a_bhimanyu/learning/1r0eunbd/file_stream (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x00000215B38E5B88>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed')). args: ('https://api.wandb.ai/files/a_bhimanyu/learning/1r0eunbd/file_stream',), kwargs: {'json': {'files': {'wandb-history.jsonl': {'offset': 3485, 'content': ['{"lrs": 0.061779986516372856, "train_losses": 0.7698876857757568, "train_acc": 0.8100199103355408, "_runtime": 8044.444728851318, "_timestamp": 1594213649.5486119, "_step": 3485}\n', '{"lrs": 0.061740628959169375, "train_losses": 0.5024967789649963, "train_acc": 0.8104084730148315, "_runtime": 8045.913047790527, "_timestamp": 1594213651.0169308, "_step": 3486}\n', '{"lrs": 0.0617012767358927, "train_losses": 0.5894423127174377, "train_acc": 0.8104248046875, "_runtime": 8047.421

wandb: Network error resolved after 0:27:16.096487, resuming normal operation.
